# MAST 30034 Assignment 1

In [777]:
import itertools

import pandas as pd
import numpy as np

#Plotly
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.express as px

AV = [0, 20, 0, 0, 0, 0]
IV = [30, 45, 60, 40, 40, 40]
DURATION_ONES = [15, 20, 25, 15, 20, 25]

N = 240
V = 441
nsrcs = 6
(x1, x2) = (21, 21)


## Question 1.1

In [730]:
# Intialize 240 x 50 shapes for TC
TC = pd.DataFrame(index=range(N), columns=np.arange(nsrcs))

In [731]:
neg_ones_duration = np.subtract(IV, DURATION_ONES)

# Generating column-wise content
for idx, (increment, arrival, duration) in enumerate(zip(IV, AV, DURATION_ONES)):
    content_array = np.array([])
    
    #Horizontally generate {0, 1} based on increment and durations
    for i in range((N//increment)+1):
        curr_row = np.hstack((np.ones(duration), np.zeros(increment-duration))) 
        content_array = np.append(content_array, curr_row)
    
    # Finalize TCs columns
    final_col = np.append(
                    np.tile(content_array, TC.shape[0]//content_array.size), 
                    content_array[:(TC.shape[0] % content_array.size)]
                ) 
    TC.loc[:, idx] = np.append(np.zeros(arrival), final_col[:240-arrival])

In [732]:
def standardize_column(df, col_no):
    col_mean = df.mean(axis=0)[col_no]
    col_std = df.std(axis=0)[col_no]

    standardize_col = np.subtract(df.loc[:, col_no], col_mean) / col_std
    
    return standardize_col

#### Building TC Subplot

In [733]:
fig = make_subplots(rows=2, cols=3,
                    subplot_titles=["Plot for TC "+str(i+1) for i in range(6)])
iterables = [[1, 2], [1, 2, 3]]

for idx, (row, col) in enumerate(itertools.product(*iterables)):
    n_col = standardize_column(TC, idx)
    fig.add_trace(
        go.Scatter(
            x=TC.index,
            y=n_col
        ),
        row=row, col=col    
    )
fig.update_layout(height=700, width=1200, title_text="TCs Source Standardized")
fig.show()

## Question 1.2

In [734]:
# Correlation Matrixs
TC.corr()

0             1             2         3             4         5
0  1.000000e+00  7.506478e-17  1.690309e-01  0.086066 -8.326673e-17  0.086066
1  7.506478e-17  1.000000e+00 -2.857143e-02  0.130931 -6.708914e-17 -0.130931
2  1.690309e-01 -2.857143e-02  1.000000e+00  0.043644 -9.711506e-17  0.130931
3  8.606630e-02  1.309307e-01  4.364358e-02  1.000000  7.745967e-01  0.600000
4 -8.326673e-17 -6.708914e-17 -9.711506e-17  0.774597  1.000000e+00  0.774597
5  8.606630e-02 -1.309307e-01  1.309307e-01  0.600000  7.745967e-01  1.000000

In [735]:
fig = px.imshow(TC.corr(),
                x=np.arange(1, 7),
                y=np.arange(1, 7))
fig.update_layout(height=600, width=700, title_text="Random Correlation Matrix")
fig.show()

## Question 1.3

**IMPORTANT NOTE that numpy start with index of zero and range excludes the end index**

In [1018]:
tmpSM = np.zeros((6, 21, 21))

In [1019]:
# i) note that numpy start with index of zero
tmpSM[0, 2:6, 2:6] = 1 

# ii)
tmpSM[1, 2:6, 15:19] = 1

# iii)
tmpSM[2, 8:13, 2:6] = 1

# iv) 
tmpSM[3, 8:13, 15:19] = 1

# v)
tmpSM[4, 15:19, 2:6] = 1

# vi)
tmpSM[5, 15:19, 15:19] = 1


In [1021]:
SM = pd.DataFrame(tmpSM.reshape((6, 441), order="F"))
SM.head()

0    1    2    3    4    5    6    7    8    9    ...  431  432  433  434  \
0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0  0.0   
1  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0  0.0   
2  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0  0.0   
3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0  0.0   
4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0  0.0   

   435  436  437  438  439  440  
0  0.0  0.0  0.0  0.0  0.0  0.0  
1  0.0  0.0  0.0  0.0  0.0  0.0  
2  0.0  0.0  0.0  0.0  0.0  0.0  
3  0.0  0.0  0.0  0.0  0.0  0.0  
4  0.0  0.0  0.0  0.0  0.0  0.0  

[5 rows x 441 columns]

In [825]:
fig = px.imshow(SM,
            width=500,
            height=500,
            aspect='auto')
fig.update_layout(
    autosize=False
)
fig.show()

## Question 1.4

In [826]:
#Gaussian Noise of Temporal Sources
gamma_t = np.random.normal( 0,     # mean
                            0.25,  # Standard Deviation
                            TC.shape #dimension
        )

#Gaussian Noise of Spatial Sources
gamma_s = np.random.normal( 0,     # mean
                            0.015,  # Standard Deviation
                            SM.shape #dimension
        )

# product of gamma_t and gamma_s
gamma_v = np.dot(gamma_t, gamma_s)

#Correlations within the sources
R2_t = np.corrcoef(gamma_t.T)
R2_s = np.corrcoef(gamma_s)


In [827]:
fig = make_subplots(rows=1, cols=2, subplot_titles=["Temporal Source", "Spatial Source"])
fig.add_trace(go.Heatmap(z=R2_t), row=1, col=1)
fig.add_trace(go.Heatmap(z=R2_s), row=1, col=2)
fig.update_layout(height=500, width=1000, title_text="Correlation Matrix for Guassian Noises")
fig.show()

In [828]:
fig = px.imshow(pd.DataFrame(gamma_v).corr().iloc[0:9, 0:9])
fig.update_layout(height=500, width=500, title_text=u"Correlation Matrix of \u0393<sub>t</sub>\u0393<sub>s</sub>")
fig.show()

In [829]:
fig = make_subplots(rows=3, cols=1, 
                    subplot_titles=["Gaussian Noise distributions for Temporal", 
                                    "Gaussian Noise Distribution for Spatial", 
                                    "Product Distribution of Temporal and Spatial"])

fig.add_trace(go.Histogram(x=gamma_t.reshape(1, np.product(gamma_t.shape))[0]), row=1, col=1)
fig.add_trace(go.Histogram(x=gamma_s.reshape(1, np.product(gamma_s.shape))[0]), row=2, col=1)
fig.add_trace(go.Histogram(x=gamma_v.reshape(1, np.product(gamma_v.shape))[0]), row=3, col=1)

fig.update_layout(height=950, width=1000, title_text="Gaussian Noise distributions")
fig.show()

### Question 1.5

In [923]:
X = np.dot(np.add(TC.to_numpy(), gamma_t), np.add(SM.to_numpy(), gamma_s))
X = pd.DataFrame(X)
print("TC+Gamma_t", np.add(TC.to_numpy(), gamma_t).shape)
print("TC+Gamma_s", np.add(SM.to_numpy(), gamma_s).shape)
X.shape

TC+Gamma_t (240, 6)
TC+Gamma_s (6, 441)


(240, 441)

In [926]:
# Randomly choose 101 columns from X
X_sample = X.sample(n=101, axis='columns').copy()

In [927]:
fig = px.line(X_sample, y = X_sample.columns, title="101 X's Time series")
fig.update_layout(showlegend=False, xaxis_title="Time Unit", yaxis_title="Value")
fig.show()

In [928]:
X_var = X.var(axis=0)
fig = px.line(y = X_var, title="Variance of 441 Variables")
fig.show()

In [1006]:
#Standardize X
X_std = pd.DataFrame(index=np.arange(X.shape[0]), columns=np.arange(X.shape[1]))
for idx in range(len(X.columns)):
    X_std[idx] = standardize_column(X, idx)

### Question 2.1
Consider $A_{LSR}=(D^TD)^{-1}D^TX$

In [930]:
D = TC.to_numpy().copy()
A_lsr = np.dot(
            np.linalg.inv(np.dot(D.T, D)), 
            np.dot(D.T, X.to_numpy())
        )

Establish $D_{LSR} = XA^T_{LSR}$

In [931]:
D_lsr = np.dot(X.to_numpy(), A_lsr.T)
D_lsr = pd.DataFrame(D_lsr)

Plot Six Retrieving sources

In [932]:
fig = make_subplots(rows=6, cols=2, shared_yaxes=False)

for idx, row in enumerate(range(1, 7)):
    spatial_map = A_lsr[idx].reshape((21, 21), order="F")
    fig.add_trace(go.Heatmap(z=spatial_map), row=row, col=1)
    fig.update_yaxes(autorange="reversed", row=row, col=1)
    fig.add_trace(
        go.Scatter(
            y=D_lsr[idx]
        ),
        row=row, col=2
    )
    fig.update_yaxes(autorange=True, row=row, col=2)
fig.update_layout(height=1600, width=1000, title_text="Retrieved Source", showlegend=False)
fig.show()

In [982]:
fig = px.scatter(x=D_lsr[3-1], y=standardize_column(X, 30-1), trendline="ols")

fig.update_layout(height=500, 
                width=800,     
                xaxis_title="3rd D<sub>SLR</sub>",
                yaxis_title="30th Column of Standardized X",
                title_text="3rd D<sub>SLR</sub> vs. 30th Column of Standardized X"
    )
fig.show()

### Question 2.2

Considering 
$$
\begin{aligned}
A_{RR} &=(D^TD+\tilde{\lambda} I)D^TX\\
D_{RR} &= XA_{RR}^T
\end{aligned}
$$

In [934]:
LAMBDA_HAT = 0.99

A_rr = np.dot(
            np.linalg.inv(np.dot(D.T, D) + LAMBDA_HAT * np.identity(D.shape[1])),
            np.dot(D.T, X.to_numpy()) 
        )
D_rr = np.dot(X.to_numpy(), A_rr.T)

Maximum Absolute correlation based on their six columns, i.e. $c_{TLSR}$ and $c_{TRR}$

In [935]:
c_tlsr = TC.corrwith(pd.DataFrame(D_lsr), axis=0)
c_trr = TC.corrwith(pd.DataFrame(D_rr), axis=0)

In [936]:
print(sum(c_trr), sum(c_tlsr),  "||sum(c_tlsr) < sum(c_trr) = ", sum(c_tlsr)< sum(c_trr))

4.5052897093540265 4.463646047872606 ||sum(c_tlsr) < sum(c_trr) =  True


### Plot the Graph  

In [937]:
LAMBDA_PLOT = 1000
A_rr_plot = np.dot(
                np.linalg.inv(np.dot(D.T, D) + LAMBDA_PLOT * np.identity(D.shape[1])),
                np.dot(D.T, X.to_numpy()) 
            )
A_lsr_plot = A_lsr.copy()

In [983]:
fig = px.scatter(x=A_rr_plot[0], y=A_lsr_plot[0])
fig.update_layout(
    xaxis_title="First Vector of A<sub>RR</sub>",
    yaxis_title="First Vector of A<sub>LSR</sub>",
    title=u"A<sub>LSR</sub> vs. A<sub>RR</sub> for \u03BB = 1000",
    height=500, 
    width=800, 
)

fig.update_xaxes(autorange="reversed")
fig.show()

### Question 2.3

In [941]:
rho_lst = np.arange(0, 1.05, 0.05)

LR Code as implemented in *pg.3* of **Asignment 1 Spec**

In [965]:
def compute_lasso_reg(rho, TC, X):
    step = 1 / (np.linalg.norm(np.dot(TC, TC.T)) * 1.1)
    thr = rho * N * step

    A_o = np.zeros((nsrcs, 1))  #6, 1
    A = np.zeros((nsrcs, 1))
    A_lr = np.zeros((nsrcs, x1 * x2)) #6 441
    
    for k in range(x1 * x2):  # 441 iters for 21 x 21
        A = A_o + step * np.dot(TC.T, (X.to_numpy()[:, k] - np.dot(TC, A_o).T).T)
        A = (1/(1+thr)) * (np.sign(A) * np.maximum(np.zeros((nsrcs, 1)), np.absolute(A) - thr))
        for i in range(10):
            A_o = A
            A = A_o + step * np.dot(TC.T, (X.to_numpy()[:, k] - np.dot(TC, A_o).T).T)
            A = (1/(1+thr)) * (np.sign(A) * np.maximum(np.zeros((nsrcs, 1)), np.subtract(np.absolute(A), thr)))
        A_lr[:, k] = A.T
    return A_lr

In [976]:
MAX_RHO_SAMPLES = 21
# rho_samples = np.sort(np.random.choice(rho_lst, MAX_RHO_SAMPLES, replace=False))
rho_samples = rho_lst[2:MAX_RHO_SAMPLES+2]
rho_samples


array([0.1 , 0.15, 0.2 , 0.25, 0.3 , 0.35, 0.4 , 0.45, 0.5 , 0.55, 0.6 ,
       0.65, 0.7 , 0.75, 0.8 , 0.85, 0.9 , 0.95, 1.  ])

In [977]:
def create_standardized_X(TC, SM):
    #Gaussian Noise of Temporal Sources
    gamma_t = np.random.normal( 0,     # mean
                                0.25,  # Standard Deviation
                                TC.shape #dimension
                              )
    #Gaussian Noise of Spatial Sources
    gamma_s = np.random.normal( 0,     # mean
                                0.015,  # Standard Deviation
                                SM.shape #dimension
                            )
    X = np.dot(np.add(TC.to_numpy(), gamma_t), np.add(SM.to_numpy(), gamma_s))
    X = pd.DataFrame(X)
    for idx in range(len(X.shape)):
        X[idx] = standardize_column(X, idx)
    return X

In [978]:
MSE_lst = []
for rho in rho_samples:
    MSE = 0
    for i in range(10):
        # Create new standardized X for each iterations
        X = create_standardized_X(TC, SM)
        A_lr = compute_lasso_reg(rho, TC, X)
        D_lr = np.dot(X.to_numpy(), A_lr.T)
        MSE += np.sum(np.sum(np.power(X-np.dot(D_lr, A_lr), 2))) / (N * V)
    MSE /= 10
    MSE_lst.append(MSE)


In [979]:
MSE_lst

[5.890084372000502,
 2.45656006173114,
 0.8927793361978343,
 0.29290729738590454,
 0.10155336550282164,
 0.06801375780480459,
 0.08597338452527327,
 0.10616238585245334,
 0.12048814190358006,
 0.12727825650652755,
 0.12919660737142624,
 0.13010337512296438,
 0.1296045114826169,
 0.1303432445532982,
 0.130824378751953,
 0.12943441550941018,
 0.12925581476507778,
 0.12943665290227435,
 0.1283025653631382]

In [984]:
fig = px.line(y=MSE_lst, x=rho_samples, title=u"\u03C1 Sample values vs. MSE")
fig.update_layout(
    height=500, 
    width=800, 
)
fig.show()

### Question 2.4

In [1039]:
rho_min_mse = 0.35
A_lr = compute_lasso_reg(rho_min_mse, TC, X_std)
D_lr = np.dot(X_std.to_numpy(), A_lr.T)

# TC Correlations
c_trr = TC.corrwith(pd.DataFrame(D_rr), axis=0)
c_tlr = TC.corrwith(pd.DataFrame(D_lr), axis=0)

#SM Correlations, as SM correlation were transposed in the first place i.e. axis=1
c_srr = SM.corrwith(pd.DataFrame(A_rr), axis=1) 
c_slr = SM.corrwith(pd.DataFrame(A_lr), axis=1)

In [1042]:
print(sum(c_trr), sum(c_tlr),  "; sum(c_tlr) > sum(c_trr) = ", sum(c_trr) < sum(c_tlr))
print(sum(c_srr), sum(c_slr),  "; sum(c_tlr) > sum(c_trr) = ", sum(c_srr) < sum(c_slr))

4.5052897093540265 5.422827742243714 ; sum(c_tlr) > sum(c_trr) =  True
2.600946180844616 5.295883390373641 ; sum(c_tlr) > sum(c_trr) =  True


In [1047]:
print("A_rr shape:", A_rr.shape)
print("A_lr shape:", A_lr.shape)
print("D_rr shape:", D_rr.shape)
print("D_lr shape:", D_lr.shape)
print("SM shape:", SM.shape)
print("TC shape:", TC.shape)

A_rr shape: (6, 441)
A_lr shape: (6, 441)
D_rr shape: (240, 6)
D_lr shape: (240, 6)
SM shape: (6, 441)
TC shape: (240, 6)


In [1060]:
# 4 random choice of column
rand_col = np.random.choice(np.arange(A_rr.shape[0]), 4, replace=False)


array([3, 4, 0, 5])

In [1073]:
fig = make_subplots(rows=2, 
                    cols=2,
                    subplot_titles=["A<sub>RR</sub> Plot with Selected Columns",
                                    "A<sub>LR</sub> Plot with Selected Columns",
                                    "D<sub>RR</sub> Plot with Selected Columns",
                                    "D<sub>LR</sub> Plot with Selected Columns"
                                    ]
                    )

for rand_num in rand_col:
    fig.add_trace(go.Scatter(y=A_rr[rand_num], mode='lines'),
        row=1, col=1
    )
    fig.add_trace(go.Scatter(y=A_lr[rand_num], mode='lines'),
        row=1, col=2
    )
    fig.add_trace(go.Scatter(y=D_rr.T[rand_num], mode='lines'),
        row=2, col=1
    )
    fig.add_trace(go.Scatter(y=D_lr.T[rand_num], mode='lines'),
        row=2, col=2
    )

fig.update_layout(showlegend=False, title="Column Estimates for D and A")
fig.show()

### Question 2.5

In [1083]:
U, V, W = np.linalg.svd(TC.to_numpy(), full_matrices=False)

In [1084]:
print("U Shape: ", U.shape)
print("V Shape: ", V.shape)
print("W Shape: ", W.shape)

U Shape:  (240, 6)
V Shape:  (6,)
W Shape:  (6, 6)


In [1082]:
print("PC position where e\'value are the smallest: ", np.argmin(V)+1)

PC position where e'value are the smallest:  6


In [1098]:
Z = pd.DataFrame(U)

In [1101]:
fig = make_subplots(rows=6, cols=2)

for i in range(6):
    fig.add_trace(go.Scatter(y=Z[i], mode='lines'),
            row=i+1, col=1
        )
    fig.add_trace(go.Scatter(y=TC[i], mode='lines'),
            row=i+1, col=2
        )
fig.update_layout(title="Z vs. TC for 6 Respective Columns", showlegend=False, height=700)
fig.show()